# **Covid19 Analysis**

In [167]:
import pandas as pd
import numpy as np
from graphic_cov import visualize_covid_cases
import matplotlib.pyplot as plt
import folium
import plotly.express as px
from plotly.subplots import make_subplots
from datetime import datetime, timedelta, date

In [56]:
# Dataset
df_confirmed = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv')
df_deaths = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_global.csv')
df_recovered = pd.read_csv('https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_recovered_global.csv')
df_covid19 = pd.read_csv("https://raw.githubusercontent.com/CSSEGISandData/COVID-19/web-data/data/cases_country.csv")
df_table = pd.read_csv("https://raw.githubusercontent.com/CSSEGISandData/COVID-19/web-data/data/cases_time.csv",parse_dates=['Last_Update'])

In [57]:
df_confirmed = df_confirmed.rename(columns={"Province/State":"State","Country/Region": "Country"})
df_deaths = df_deaths.rename(columns={"Province/State":"State","Country/Region": "Country"})
df_recovered = df_recovered.rename(columns={"Province/State":"State","Country/Region": "Country"})

In [58]:

# extract dates
dates = df_confirmed.columns[4:]

# melt dataframes in longer format
df_confirmed_long = df_confirmed.melt(id_vars=['State', 'Country', 'Lat', 'Long'], 
                            value_vars=dates, var_name='Date', value_name='Confirmed')

df_deaths_long = df_deaths.melt(id_vars=['State', 'Country', 'Lat', 'Long'], 
                            value_vars=dates, var_name='Date', value_name='Deaths')

df_recovered_long = df_recovered.melt(id_vars=['State', 'Country', 'Lat', 'Long'], 
                            value_vars=dates, var_name='Date', value_name='Recovered')

print(df_confirmed_long.shape)
print(df_deaths_long.shape)
print(df_recovered_long.shape)

(31654, 6)
(31654, 6)
(30107, 6)


In [59]:
covid19_table = pd.merge(left=df_confirmed_long, right=df_deaths_long, how='left',
                      on=['State', 'Country', 'Date', 'Lat', 'Long'])
covid19_table = pd.merge(left=covid19_table, right=df_recovered_long, how='left',
                      on=['State', 'Country', 'Date', 'Lat', 'Long'])

covid19_table.head()

State      Country      Lat     Long     Date  Confirmed  Deaths  Recovered
0   NaN  Afghanistan  33.0000  65.0000  1/22/20          0       0        0.0
1   NaN      Albania  41.1533  20.1683  1/22/20          0       0        0.0
2   NaN      Algeria  28.0339   1.6596  1/22/20          0       0        0.0
3   NaN      Andorra  42.5063   1.5218  1/22/20          0       0        0.0
4   NaN       Angola -11.2027  17.8739  1/22/20          0       0        0.0

In [60]:
covid19_table.shape

(31654, 8)

In [61]:
covid19_table.isna().sum()

State        22015
Country          0
Lat              0
Long             0
Date             0
Confirmed        0
Deaths           0
Recovered     2023
dtype: int64

In [62]:

covid19_table['Recovered'] = covid19_table['Recovered'].fillna(0)
covid19_table['Recovered'] = covid19_table['Recovered'].astype('int')
covid19_table.isna().sum()


State        22015
Country          0
Lat              0
Long             0
Date             0
Confirmed        0
Deaths           0
Recovered        0
dtype: int64

In [63]:
my_dict_pycountry = {
    'US': 'USA', 
    'Korea, South': 'South Korea', 
    'Taiwan*': 'Taiwan',
    'Congo (Kinshasa)': 'Democratic Republic of the Congo',
    "Cote d'Ivoire": "Côte d'Ivoire",
    "Reun:ion": "Réunion",
    "Congo (Brazzaville)": "Republic of the Congo",
    'Bahamas, The': 'Bahamas',
    'Gambia, The': 'Gambia'
     }
for key, value in my_dict_pycountry.items():
        covid19_table.loc[covid19_table['Country'] == key, "Country"] = value

In [64]:

# removing
# =======

# removing canada's recovered values
covid19_table = covid19_table[covid19_table['State'].str.contains('Recovered')!=True]

# removing county wise data to avoid double counting
covid19_table = covid19_table[covid19_table['State'].str.contains(',')!=True]

In [65]:
covid19_table.shape

(31535, 8)

In [66]:

# new values
feb_12_conf = {'Hubei' : 34874}

In [67]:
# function to change value
def change_val(date, ref_col, val_col, dtnry):
    for key, val in dtnry.items():
        covid19_table.loc[(covid19_table['Date']==date) & (covid19_table[ref_col]==key), val_col] = val

In [68]:
change_val('2/12/20', 'State', 'Confirmed', feb_12_conf)

In [69]:
covid19_table[(covid19_table['Date']=='2/12/20') & (covid19_table['State']=='Hubei')]

State Country      Lat      Long     Date  Confirmed  Deaths  Recovered
5648  Hubei   China  30.9756  112.2707  2/12/20      34874    1068       2686

In [70]:
covid19_table.sample(6)

State             Country      Lat      Long     Date  \
11665               NaN           Venezuela   6.4238  -66.5897   3/5/20   
15724               NaN            Bulgaria  42.7339   25.4858  3/21/20   
3227            Alberta              Canada  53.9333 -116.5765   2/3/20   
16278            Fujian               China  26.0789  117.9874  3/23/20   
834    British Columbia              Canada  49.2827 -123.1207  1/25/20   
2490                NaN  Dominican Republic  18.7357  -70.1627  1/31/20   

       Confirmed  Deaths  Recovered  
11665          0       0          0  
15724        163       3          3  
3227           0       0          0  
16278        313       1        295  
834            0       0          0  
2490           0       0          0

In [71]:
#covid19_table.to_csv('covid_19_clean_complete.csv', index=False)


State       Country        Lat        Long       Date  \
26205           NaN         Syria  34.802075   38.996815 2020-04-29   
18              NaN       Bahamas  25.034300  -77.396300 2020-01-22   
23853           NaN       Andorra  42.506300    1.521800 2020-04-21   
16895           NaN  South Africa -30.559500   22.937500 2020-03-25   
19724     St Martin        France  18.070800  -63.050100 2020-04-05   
23100  Saskatchewan        Canada  52.939900 -106.450900 2020-04-18   

       Confirmed  Deaths  Recovered  
26205         43       3          0  
18             0       0          0  
23853        717      37        282  
16895        709       0         12  
19724         32       2          7  
23100        313       4          0

In [77]:
covid19_table['Date'] = pd.to_datetime(covid19_table['Date'])

In [78]:
covid19_table.sample(6)

State         Country      Lat      Long       Date  \
1367   Grand Princess          Canada  37.6489 -122.6655 2020-01-27   
12825          Hainan           China  19.1959  109.7453 2020-03-10   
7115              NaN         Somalia   5.1521   46.1996 2020-02-17   
28128             NaN        Slovenia  46.1512   14.9955 2020-05-06   
30810       Gibraltar  United Kingdom  36.1408   -5.3536 2020-05-16   
9499              NaN     Saint Lucia  13.9094  -60.9789 2020-02-26   

       Confirmed  Deaths  Recovered  
1367           0       0          0  
12825        168       6        159  
7115           0       0          0  
28128       1448      99        246  
30810        147       0        145  
9499           0       0          0

In [84]:
# Cleaning data
# =============

# fixing Country values
covid19_table.loc[covid19_table['State']=='Greenland', 'Country'] = 'Greenland'

# Active Case = confirmed - deaths - recovered
covid19_table['Active'] = (covid19_table['Confirmed'] - covid19_table['Deaths'] - covid19_table['Recovered'])

# filling missing values 
covid19_table[['State']] = covid19_table[['State']].fillna('')
covid19_table[['Confirmed', 'Deaths', 'Recovered', 'Active']] = covid19_table[['Confirmed', 'Deaths', 'Recovered', 'Active']].fillna(0)

# fixing datatypes
covid19_table['Recovered'] = covid19_table['Recovered'].astype(int)

covid19_table.sample(6)

State     Country      Lat      Long       Date  Confirmed  \
4697                       Norway  60.4720    8.4689 2020-02-08          0   
3915                   San Marino  43.9424   12.4578 2020-02-05          0   
5091   Grand Princess      Canada  37.6489 -122.6655 2020-02-10          0   
22570                  Uzbekistan  41.3775   64.5853 2020-04-15       1302   
18029                      Taiwan  23.7000  121.0000 2020-03-29        298   
4825   Grand Princess      Canada  37.6489 -122.6655 2020-02-09          0   

       Deaths  Recovered  Active  
4697        0          0       0  
3915        0          0       0  
5091        0          0       0  
22570       4        107    1191  
18029       2         30     266  
4825        0          0       0

In [87]:
# Grouped by day, country
# =======================

covid19_country = covid19_table.groupby(['Date', 'Country'])['Confirmed', 'Deaths', 'Recovered', 'Active'].sum().reset_index()

# new cases ======================================================
temp = covid19_country.groupby(['Country', 'Date', ])['Confirmed', 'Deaths', 'Recovered']
temp = temp.sum().diff().reset_index()

mask = temp['Country'] != temp['Country'].shift(1)

temp.loc[mask, 'Confirmed'] = np.nan
temp.loc[mask, 'Deaths'] = np.nan
temp.loc[mask, 'Recovered'] = np.nan

# renaming columns
temp.columns = ['Country', 'Date', 'New cases', 'New deaths', 'New recovered']
# =================================================================

# merging new values
covid19_country = pd.merge(covid19_country, temp, on=['Country', 'Date'])

# filling na with 0
covid19_country = covid19_country.fillna(0)

# fixing data types
cols = ['New cases', 'New deaths', 'New recovered']
covid19_country[cols] = covid19_country[cols].astype('int')

covid19_country['New cases'] = covid19_country['New cases'].apply(lambda x: 0 if x<0 else x)

covid19_country.sample(6)

Date                   Country  Confirmed  Deaths  Recovered  \
3696  2020-02-10                    Malawi          0       0          0   
2123  2020-02-02             Côte d'Ivoire          0       0          0   
11888 2020-03-24               Timor-Leste          1       0          0   
978   2020-01-27  Central African Republic          0       0          0   
14361 2020-04-06                     Yemen          0       0          0   
8352  2020-03-06                     China      80690    3044      53944   

       Active  New cases  New deaths  New recovered  
3696        0          0           0              0  
2123        0          0           0              0  
11888       1          0           0              0  
978         0          0           0              0  
14361       0          0           0              0  
8352    23702        153          29           1652

In [89]:
# Day wise
# ========

# table
day_wise = covid19_country.groupby('Date')['Confirmed', 'Deaths', 'Recovered', 'Active', 'New cases', 'New deaths'].sum().reset_index()

# number cases per 100 cases
day_wise['Deaths / 100 Cases'] = round((day_wise['Deaths']/day_wise['Confirmed'])*100, 2)
day_wise['Recovered / 100 Cases'] = round((day_wise['Recovered']/day_wise['Confirmed'])*100, 2)
day_wise['Deaths / 100 Recovered'] = round((day_wise['Deaths']/day_wise['Recovered'])*100, 2)

# no. of countries
day_wise['No. of countries'] = covid19_country[covid19_country['Confirmed']!=0].groupby('Date')['Country'].unique().apply(len).values

# fillna by 0
cols = ['Deaths / 100 Cases', 'Recovered / 100 Cases', 'Deaths / 100 Recovered']
day_wise[cols] = day_wise[cols].fillna(0)

day_wise.head()

Date  Confirmed  Deaths  Recovered  Active  New cases  New deaths  \
0 2020-01-22        555      17         28     510          0           0   
1 2020-01-23        654      18         30     606         99           1   
2 2020-01-24        941      26         36     879        287           8   
3 2020-01-25       1434      42         39    1353        493          16   
4 2020-01-26       2118      56         52    2010        684          14   

   Deaths / 100 Cases  Recovered / 100 Cases  Deaths / 100 Recovered  \
0                3.06                   5.05                   60.71   
1                2.75                   4.59                   60.00   
2                2.76                   3.83                   72.22   
3                2.93                   2.72                  107.69   
4                2.64                   2.46                  107.69   

   No. of countries  
0                 6  
1                 8  
2                 9  
3                11  
4                13

In [91]:
# Country wise
# ============

# getting latest values
country_wise = covid19_country[covid19_country['Date']==max(covid19_country['Date'])].reset_index(drop=True).drop('Date', axis=1)

# group by country
country_wise = country_wise.groupby('Country')['Confirmed', 'Deaths', 'Recovered', 'Active', 'New cases'].sum().reset_index()

# per 100 cases
country_wise['Deaths / 100 Cases'] = round((country_wise['Deaths']/country_wise['Confirmed'])*100, 2)
country_wise['Recovered / 100 Cases'] = round((country_wise['Recovered']/country_wise['Confirmed'])*100, 2)
country_wise['Deaths / 100 Recovered'] = round((country_wise['Deaths']/country_wise['Recovered'])*100, 2)

cols = ['Deaths / 100 Cases', 'Recovered / 100 Cases', 'Deaths / 100 Recovered']
country_wise[cols] = country_wise[cols].fillna(0)

country_wise.head()

Country  Confirmed  Deaths  Recovered  Active  New cases  \
0  Afghanistan       7653     178        850    6625        581   
1      Albania        949      31        742     176          1   
2      Algeria       7377     561       3746    3070        176   
3      Andorra        761      51        628      82          0   
4       Angola         52       3         17      32          2   

   Deaths / 100 Cases  Recovered / 100 Cases  Deaths / 100 Recovered  
0                2.33                  11.11                   20.94  
1                3.27                  78.19                    4.18  
2                7.60                  50.78                   14.98  
3                6.70                  82.52                    8.12  
4                5.77                  32.69                   17.65

In [94]:
# load population dataset
pop = pd.read_csv("population_by_country_2020.csv")

# select only population
pop = pop.iloc[:, :2]

# rename column names
pop.columns = ['Country/Region', 'Population']
pop = pop.rename(columns={"Country/Region": "Country"})
# merged data
country_wise = pd.merge(country_wise, pop, on='Country', how='left')

# # update population
# cols = ['Burma', 'Congo (Brazzaville)', 'Congo (Kinshasa)', "Cote d'Ivoire", 'Czechia', 
#         'Kosovo', 'Saint Kitts and Nevis', 'Saint Vincent and the Grenadines', 
#         'Taiwan*', 'US', 'West Bank and Gaza', 'Sao Tome and Principe']
# pops = [54409800, 89561403, 5518087, 26378274, 10708981, 1793000, 
#         53109, 110854, 23806638, 330541757, 4543126, 219159]
# for c, p in zip(cols, pops):
#     country_wise.loc[country_wise['Country/Region']== c, 'Population'] = p
    
# missing values
# country_wise.isna().sum()
# country_wise[country_wise['Population'].isna()]['Country/Region'].tolist()

# Cases per population
country_wise['Cases / Million People'] = round((country_wise['Confirmed'] / country_wise['Population']) * 1000000)

country_wise.head()

Country  Confirmed  Deaths  Recovered  Active  New cases  \
0  Afghanistan       7653     178        850    6625        581   
1      Albania        949      31        742     176          1   
2      Algeria       7377     561       3746    3070        176   
3      Andorra        761      51        628      82          0   
4       Angola         52       3         17      32          2   

   Deaths / 100 Cases  Recovered / 100 Cases  Deaths / 100 Recovered  \
0                2.33                  11.11                   20.94   
1                3.27                  78.19                    4.18   
2                7.60                  50.78                   14.98   
3                6.70                  82.52                    8.12   
4                5.77                  32.69                   17.65   

   Population  Cases / Million People  
0  38742911.0                   198.0  
1   2878420.0                   330.0  
2  43685618.0                   169.0  
3     77240.0                  9852.0  
4  32644783.0                     2.0

In [98]:
today = covid19_table[covid19_table['Date']==max(covid19_table['Date'])].reset_index(drop=True).drop('Date', axis=1)[['Country', 'Confirmed']]
last_week = covid19_table[covid19_table['Date']==max(covid19_table['Date'])-timedelta(days=7)].reset_index(drop=True).drop('Date', axis=1)[['Country', 'Confirmed']]

temp = pd.merge(today, last_week, on='Country', suffixes=(' today', ' last week'))

# temp = temp[['Country/Region', 'Confirmed last week']]
temp['1 week change'] = temp['Confirmed today'] - temp['Confirmed last week']

temp = temp[['Country', 'Confirmed last week', '1 week change']]

country_wise = pd.merge(country_wise, temp, on='Country')

country_wise['1 week % increase'] = round(country_wise['1 week change']/country_wise['Confirmed last week']*100, 2)

country_wise.head()

Country  Confirmed  Deaths  Recovered  Active  New cases  \
0  Afghanistan       7653     178        850    6625        581   
1      Albania        949      31        742     176          1   
2      Algeria       7377     561       3746    3070        176   
3      Andorra        761      51        628      82          0   
4       Angola         52       3         17      32          2   

   Deaths / 100 Cases  Recovered / 100 Cases  Deaths / 100 Recovered  \
0                2.33                  11.11                   20.94   
1                3.27                  78.19                    4.18   
2                7.60                  50.78                   14.98   
3                6.70                  82.52                    8.12   
4                5.77                  32.69                   17.65   

   Population  Cases / Million People  Confirmed last week  1 week change  \
0  38742911.0                   198.0                 4963           2690   
1   2878420.0                   330.0                  876             73   
2  43685618.0                   169.0                 6067           1310   
3     77240.0                  9852.0                  758              3   
4  32644783.0                     2.0                   45              7   

   1 week % increase  
0              54.20  
1               8.33  
2              21.59  
3               0.40  
4              15.56

In [99]:
country_wise[country_wise['Cases / Million People'].isna()]

Country  Confirmed  Deaths  Recovered   Active  \
90                               Burma        193       6        104       83   
1389                           Czechia       8647     302       5726     2619   
1391  Democratic Republic of the Congo       1629      61        290     1278   
1396                  Diamond Princess        712      13        651       48   
1560                            Kosovo        989      29        769      191   
1572                        MS Zaandam          9       2          0        7   
1622             Republic of the Congo        420      15        132      273   
1626             Saint Kitts and Nevis         15       0         15        0   
1628  Saint Vincent and the Grenadines         17       0         14        3   
1630             Sao Tome and Principe        251       8          4      239   
1659                               USA    1528568   91921     289392  1147255   
1788                West Bank and Gaza        391       2        346       43   

      New cases  Deaths / 100 Cases  Recovered / 100 Cases  \
90            2                3.11                  53.89   
1389         61                3.49                  66.22   
1391         91                3.74                  17.80   
1396          0                1.83                  91.43   
1560         34                2.93                  77.76   
1572          0               22.22                   0.00   
1622          8                3.57                  31.43   
1626          0                0.00                 100.00   
1628          0                0.00                  82.35   
1630          5                3.19                   1.59   
1659      20260                6.01                  18.93   
1788          3                0.51                  88.49   

      Deaths / 100 Recovered  Population  Cases / Million People  \
90                      5.77         NaN                     NaN   
1389                    5.27         NaN                     NaN   
1391                   21.03         NaN                     NaN   
1396                    2.00         NaN                     NaN   
1560                    3.77         NaN                     NaN   
1572                     inf         NaN                     NaN   
1622                   11.36         NaN                     NaN   
1626                    0.00         NaN                     NaN   
1628                    0.00         NaN                     NaN   
1630                  200.00         NaN                     NaN   
1659                   31.76         NaN                     NaN   
1788                    0.58         NaN                     NaN   

      Confirmed last week  1 week change  1 week % increase  
90                    180             13               7.22  
1389                 8221            426               5.18  
1391                 1102            527              47.82  
1396                  712              0               0.00  
1560                  919             70               7.62  
1572                    9              0               0.00  
1622                  333             87              26.13  
1626                   15              0               0.00  
1628                   17              0               0.00  
1630                  208             43              20.67  
1659              1369376         159192              11.63  
1788                  375             16               4.27

In [151]:
# color pallette
cnf, dth, rec, act = '#393e46', '#ff2e63', '#21bf73', '#fe9801' 
temp = covid19_table.groupby('Date')['Confirmed', 'Deaths', 'Recovered', 'Active'].sum().reset_index()
temp = temp[temp['Date']==max(temp['Date'])].reset_index(drop=True)
tm = temp.melt(id_vars="Date", value_vars=['Active', 'Deaths', 'Recovered'])
tm = tm.rename(columns={"Date":"Confirmed"})
fig = px.treemap(tm, path=["Confirmed","variable"], values="value", height=300, width=1200,color ="variable",
                 color_discrete_map={'(?)':'yellow', 'Active':act, 'Deaths':dth,'Recovered':rec })
fig.data[0].textinfo = 'label+text+value'
fig.show()

In [152]:
temp = covid19_table.groupby('Date')['Recovered', 'Deaths', 'Active'].sum().reset_index()
temp = temp.melt(id_vars="Date", value_vars=['Recovered', 'Deaths', 'Active'],
                 var_name='Case', value_name='Count')
temp.head()

fig = px.area(temp, x="Date", y="Count", color='Case', height=600,
             title='Cases over time', color_discrete_sequence = [rec, dth, act])
fig.update_layout(xaxis_rangeslider_visible=True)
fig.show()

In [160]:
world_map = folium.Map(location=[10,0], tiles="cartodbpositron", zoom_start=2,max_zoom=6,min_zoom=2)
temp = covid19_table[covid19_table['Date'] == max(full_table['Date'])]
for i in range(0,len(temp)):
    folium.Circle(
        location=[temp.iloc[i]['Lat'], temp.iloc[i]['Long']],
        tooltip = "<h5 style='text-align:center;font-weight: bold'>"+temp.iloc[i]['Country']+"</h5>"+
                    "<div style='text-align:center;'>"+str(np.nan_to_num(temp.iloc[i]['State']))+"</div>"+
                    "<hr style='margin:10px;'>"+
                    "<ul style='color: #444;list-style-type:circle;align-item:left;padding-left:20px;padding-right:20px'>"+
        "<li>Confirmed: "+str(temp.iloc[i]['Confirmed'])+"</li>"+
        "<li>Deaths:   "+str(temp.iloc[i]['Deaths'])+"</li>"+
        "<li>Recovered:   "+str(temp.iloc[i]['Recovered'])+"</li>"+
        "</ul>"
        ,
        radius=(int((np.log(df_confirmed.iloc[i,-1]+1.00001)))+0.2)*50000,
        color='#ff6600',
        fill_color='#ff8533',
        fill=True).add_to(world_map)
world_map

In [172]:
# Over the time

fig = px.choropleth(covid19_country, locations="Country", locationmode='country names', color=np.log(covid19_country["Confirmed"]), 
                    hover_name="Country", animation_frame=covid19_country["Date"].dt.strftime('%Y-%m-%d'),
                    title='Cases over time', color_continuous_scale=px.colors.sequential.Purp)
fig.update(layout_coloraxis_showscale=False)
fig.show()

In [173]:
fig_c = px.choropleth(country_wise, locations="Country", locationmode='country names', 
                      color=np.log(country_wise["Confirmed"]), hover_name="Country", 
                      hover_data=['Confirmed'], color_continuous_scale="Purp")

# Deaths
temp = country_wise[country_wise['Deaths']>0]
fig_d = px.choropleth(temp, locations="Country", locationmode='country names',
                      color=np.log(temp["Deaths"]), hover_name="Country", 
                      hover_data=['Deaths'], color_continuous_scale="Viridis")

# Plot
fig = make_subplots(rows=1, cols=2, subplot_titles = ['Confirmed', 'Deaths'],
                    specs=[[{"type": "choropleth"}, {"type": "choropleth"}]])

fig.add_trace(fig_c['data'][0], row=1, col=1)
fig.add_trace(fig_d['data'][0], row=1, col=2)

fig.update(layout_coloraxis_showscale=False)

fig.show()

In [169]:
fig_c = px.bar(day_wise, x="Date", y="Confirmed", color_discrete_sequence = [act])
fig_d = px.bar(day_wise, x="Date", y="Deaths", color_discrete_sequence = [dth])
fig_r = px.bar(day_wise, x="Date", y="Recovered", color_discrete_sequence = [rec])

fig = make_subplots(rows=1, cols=3, shared_xaxes=False, horizontal_spacing=0.1,
                    subplot_titles=('Confirmed cases', 'Deaths reported', 
                                    'Recovered reported'))

fig.add_trace(fig_c['data'][0], row=1, col=1)
fig.add_trace(fig_d['data'][0], row=1, col=2)
fig.add_trace(fig_r['data'][0], row=1, col=3)


fig.update_layout(height=480)
fig.show()

# ===============================

fig_1 = px.line(day_wise, x="Date", y="Deaths / 100 Cases", color_discrete_sequence = [dth])
fig_2 = px.line(day_wise, x="Date", y="Recovered / 100 Cases", color_discrete_sequence = [rec])
fig_3 = px.line(day_wise, x="Date", y="Deaths / 100 Recovered", color_discrete_sequence = ['#333333'])

fig = make_subplots(rows=1, cols=3, shared_xaxes=False, 
                    subplot_titles=('Deaths / 100 Cases', 'Recovered / 100 Cases', 'Deaths / 100 Recovered'))

fig.add_trace(fig_1['data'][0], row=1, col=1)
fig.add_trace(fig_2['data'][0], row=1, col=2)
fig.add_trace(fig_3['data'][0], row=1, col=3)

fig.update_layout(height=480)
fig.show()

# ===================================

fig_c = px.bar(day_wise, x="Date", y="New cases", color_discrete_sequence = [act])
fig_n = px.bar(day_wise, x="Date", y="New deaths", color_discrete_sequence = [dth])
fig_d = px.bar(day_wise, x="Date", y="No. of countries", color_discrete_sequence = ['#333333'])

fig = make_subplots(rows=1, cols=3, shared_xaxes=False, horizontal_spacing=0.1,
                    subplot_titles=('No. of new cases everyday',
                                    'No. of new deaths everyday',
                                    'No. of countries'))

fig.add_trace(fig_c['data'][0], row=1, col=1)
fig.add_trace(fig_c['data'][0], row=1, col=2)
fig.add_trace(fig_d['data'][0], row=1, col=3)

fig.update_layout(height=480)
fig.show()

In [175]:
# confirmed - deaths
fig_c = px.bar(country_wise.sort_values('Confirmed').tail(15), x="Confirmed", y="Country", 
               text='Confirmed', orientation='h', color_discrete_sequence = [act])
fig_d = px.bar(country_wise.sort_values('Deaths').tail(15), x="Deaths", y="Country", 
               text='Deaths', orientation='h', color_discrete_sequence = [dth])

# recovered - active
fig_r = px.bar(country_wise.sort_values('Recovered').tail(15), x="Recovered", y="Country", 
               text='Recovered', orientation='h', color_discrete_sequence = [rec])
fig_a = px.bar(country_wise.sort_values('Active').tail(15), x="Active", y="Country", 
               text='Active', orientation='h', color_discrete_sequence = ['#333333'])

# death - recoverd / 100 cases
fig_dc = px.bar(country_wise.sort_values('Deaths / 100 Cases').tail(15), x="Deaths / 100 Cases", y="Country", 
               text='Deaths / 100 Cases', orientation='h', color_discrete_sequence = ['#f38181'])
fig_rc = px.bar(country_wise.sort_values('Recovered / 100 Cases').tail(15), x="Recovered / 100 Cases", y="Country", 
               text='Recovered / 100 Cases', orientation='h', color_discrete_sequence = ['#a3de83'])

# new cases - cases per million people
fig_nc = px.bar(country_wise.sort_values('New cases').tail(15), x="New cases", y="Country", 
               text='New cases', orientation='h', color_discrete_sequence = ['#c61951'])
temp = country_wise[country_wise['Population']>1000000]
fig_p = px.bar(temp.sort_values('Cases / Million People').tail(15), x="Cases / Million People", y="Country", 
               text='Cases / Million People', orientation='h', color_discrete_sequence = ['#741938'])

# week change, percent increase
fig_wc = px.bar(country_wise.sort_values('1 week change').tail(15), x="1 week change", y="Country", 
               text='1 week change', orientation='h', color_discrete_sequence = ['#004a7c'])
temp = country_wise[country_wise['Confirmed']>100]
fig_pi = px.bar(temp.sort_values('1 week % increase').tail(15), x="1 week % increase", y="Country", 
               text='1 week % increase', orientation='h', color_discrete_sequence = ['#005691'], 
                hover_data=['Confirmed last week', 'Confirmed'])


# plot
fig = make_subplots(rows=5, cols=2, shared_xaxes=False, horizontal_spacing=0.14, vertical_spacing=0.08,
                    subplot_titles=('Confirmed cases', 'Deaths reported', 'Recovered', 'Active cases', 
                                    'Deaths / 100 cases', 'Recovered / 100 cases', 'New cases', 
                                    'Cases / Million People', '1 week increase', '1 week % increase'))

fig.add_trace(fig_c['data'][0], row=1, col=1)
fig.add_trace(fig_d['data'][0], row=1, col=2)
fig.add_trace(fig_r['data'][0], row=2, col=1)
fig.add_trace(fig_a['data'][0], row=2, col=2)

fig.add_trace(fig_dc['data'][0], row=3, col=1)
fig.add_trace(fig_rc['data'][0], row=3, col=2)
fig.add_trace(fig_nc['data'][0], row=4, col=1)
fig.add_trace(fig_p['data'][0], row=4, col=2)

fig.add_trace(fig_wc['data'][0], row=5, col=1)
fig.add_trace(fig_pi['data'][0], row=5, col=2)


fig.update_layout(height=3000)

In [179]:
fig = px.scatter(country_wise.sort_values('Deaths', ascending=False).iloc[:20, :], 
                 x='Confirmed', y='Deaths', color='Country', size='Confirmed', height=700,
                 text='Country', log_x=True, log_y=True, title='Deaths vs Confirmed (Scale is in log10)')
fig.update_traces(textposition='top center')
fig.update_layout(showlegend=False)
fig.update_layout(xaxis_rangeslider_visible=True)
fig.show()

In [181]:
fig = px.bar(covid19_table, x="Date", y="Confirmed", color='Country', height=600,
             title='Confirmed', color_discrete_sequence = px.colors.cyclical.mygbm)
fig.show()

# =========================================

fig = px.bar(covid19_table, x="Date", y="Deaths", color='Country', height=600,
             title='Deaths', color_discrete_sequence = px.colors.cyclical.mygbm)
fig.show()

# =========================================

fig = px.bar(covid19_table, x="Date", y="New cases", color='Country', height=600,
             title='New cases', color_discrete_sequence = px.colors.cyclical.mygbm)
fig.show()

ValueError: Value of 'y' is not the name of a column in 'data_frame'. Expected one of ['State', 'Country', 'Lat', 'Long', 'Date', 'Confirmed', 'Deaths', 'Recovered', 'Active'] but received: New cases